In [12]:
from systemflow.graph import *
from systemflow.models import *
from systemflow.metrics import *
from systemflow.classifier import *

In [2]:
import pandas as pd
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import plotly.express as px
import numpy as np

# HLT Estimate (CMS)

In [3]:
b2g = pd.read_csv("hlt_data/B2G.csv")
higgs = pd.read_csv("hlt_data/higgs.csv")
muon = pd.read_csv("hlt_data/Muon.csv")
susy = pd.read_csv("hlt_data/SUSY.csv")
tracking = pd.read_csv("hlt_data/tracking.csv")
tau = pd.read_csv("hlt_data/tau.csv")

In [4]:
96 + 197 + 202 + 235 + 230 + 223 + 189 + 177 + 121

1670

In [5]:
# B2G, higgs, muon, susy, tracking, tau
# (split objects between muon, tracking, and tau)
rates = np.array([96, 235, 202/3, 189, 202/3, 202/3])

In [6]:
rates_norm = rates / np.sum(rates)

In [7]:
rates_norm

array([0.13296399, 0.32548476, 0.09325946, 0.26177285, 0.09325946,
       0.09325946])

In [8]:
b2g_rate, higgs_rate, muon_rate, susy_rate, tracking_rate, tau_rate = rates_norm

In [9]:
triggers = ["B2G", "Higgs", "Muon", "SUSY", "tracking", "tau"]
rejection_ratio = 100

In [10]:
fig = go.Figure()
fig.add_bar(x = triggers, y = rates_norm)
fig.update_layout(width = 800, height = 600)

In [13]:
def plot_trigger(data, efficiency_fit, object_fit, xaxis = "linear"):
    fig = go.Figure()
    xs = data_range(data["momentum"])
    fig.add_scatter(x = data["momentum"], y = data[" efficiency"], name="Data")
    fig.add_scatter(x = xs, y = [efficiency_fit(x) for x in xs], name="Efficiency Fit")
    fig.add_scatter(x = xs, y = 1.0 - exp_cdf(xs, object_fit.x), name = "Object Fit")
    fig.update_layout(width = 800,
                    height = 600,
                    title = "Trigger efficiency",
                    xaxis_title = "Momentum (GeV)",
                    yaxis_title = "Efficiency",
                    xaxis_type = xaxis
                    )
    return fig

In [16]:
def fit_trigger(data, empirical_rate, solver_bounds):
        #extract the dynamic range of momenta for the trigger
        xs = data_range(data["momentum"])
        #use a linear interpolation to fit the efficiency curve
        efficiency_fit = lambda x: hard_bounds(x, interp1d(data["momentum"], data[" efficiency"]), xs)
        #estimate the mean proportion of objects a trigger will activate on given an exponential input distribution of objects
        xs2 = expanded_range(xs)
        trigger_rate = lambda l: quad(lambda x: exp_dist(x, l) * efficiency_fit(x), np.min(xs2), np.max(xs2))[0]
        #calculate the gap between that and the empirical rate
        trigger_error = lambda l: np.abs(empirical_rate - trigger_rate(l))
        #minimize the gap
        soln = minimize_scalar(trigger_error, bounds = solver_bounds, method="bounded")
        return efficiency_fit, soln

In [17]:
b2g_eff, b2g_soln = fit_trigger(b2g, b2g_rate, [0.0010, 0.0050])

/var/folders/qc/b4ggx3516_qc8fy84rgtp36c0000gq/T/ipykernel_92722/2121129225.py:8: IntegrationWarning:

The maximum number of subdivisions (50) has been achieved.
  If increasing the limit yields no improvement it is advised to analyze 
  the integrand in order to determine the difficulties.  If the position of a 
  local difficulty can be determined (singularity, discontinuity) one will 
  probably gain from splitting up the interval and calling the integrator 
  on the subranges.  Perhaps a special-purpose integrator should be used.



In [18]:
b2g_soln

 message: Solution found.
 success: True
  status: 0
     fun: 0.00441017132140703
       x: 0.0049956558924794435
     nit: 14
    nfev: 14

In [19]:
plot_trigger(b2g, b2g_eff, b2g_soln)

In [20]:
b2g_turnon = find_turnon(b2g_eff, (200, 600))

In [21]:
b2g_turnon

 message: 
          Optimization terminated successfully;
          The returned value satisfies the termination criteria
          (using xtol = 1.48e-08 )
 success: True
     fun: 3.859171981979159e-09
       x: 376.7600033977237
     nit: 26
    nfev: 29

In [22]:
higgs_eff, higgs_soln = fit_trigger(higgs, higgs_rate, [0.0001, 0.0080])

/var/folders/qc/b4ggx3516_qc8fy84rgtp36c0000gq/T/ipykernel_92722/2121129225.py:8: IntegrationWarning:

The maximum number of subdivisions (50) has been achieved.
  If increasing the limit yields no improvement it is advised to analyze 
  the integrand in order to determine the difficulties.  If the position of a 
  local difficulty can be determined (singularity, discontinuity) one will 
  probably gain from splitting up the interval and calling the integrator 
  on the subranges.  Perhaps a special-purpose integrator should be used.



In [23]:
higgs_soln

 message: Solution found.
 success: True
  status: 0
     fun: 0.06890256315016108
       x: 0.0018161852335242619
     nit: 10
    nfev: 10

In [24]:
plot_trigger(higgs, higgs_eff, higgs_soln)

In [25]:
higgs_turnon = find_turnon(higgs_eff, (200, 600))

In [26]:
higgs_turnon

 message: 
          Optimization terminated successfully;
          The returned value satisfies the termination criteria
          (using xtol = 1.48e-08 )
 success: True
     fun: 3.370905976574079e-08
       x: 369.70662683662107
     nit: 25
    nfev: 28

In [27]:
muon_eff, muon_soln = fit_trigger(muon, muon_rate, [0.0001, 0.0080])

/var/folders/qc/b4ggx3516_qc8fy84rgtp36c0000gq/T/ipykernel_92722/2121129225.py:8: IntegrationWarning:

The maximum number of subdivisions (50) has been achieved.
  If increasing the limit yields no improvement it is advised to analyze 
  the integrand in order to determine the difficulties.  If the position of a 
  local difficulty can be determined (singularity, discontinuity) one will 
  probably gain from splitting up the interval and calling the integrator 
  on the subranges.  Perhaps a special-purpose integrator should be used.



In [28]:
muon_soln

 message: Solution found.
 success: True
  status: 0
     fun: 0.00027047556357030766
       x: 0.0002916257629910441
     nit: 14
    nfev: 14

In [29]:
plot_trigger(muon, muon_eff, muon_soln, "log")

In [30]:
muon_turnon = find_turnon(muon_eff, (0, 50))

In [31]:
muon_turnon

 message: 
          Optimization terminated successfully;
          The returned value satisfies the termination criteria
          (using xtol = 1.48e-08 )
 success: True
     fun: 4.588810287309286e-08
       x: 24.77513318558232
     nit: 28
    nfev: 31

In [32]:
susy_eff, susy_soln = fit_trigger(susy, susy_rate, [0.0001, 0.0080])

/var/folders/qc/b4ggx3516_qc8fy84rgtp36c0000gq/T/ipykernel_92722/2121129225.py:8: IntegrationWarning:

The maximum number of subdivisions (50) has been achieved.
  If increasing the limit yields no improvement it is advised to analyze 
  the integrand in order to determine the difficulties.  If the position of a 
  local difficulty can be determined (singularity, discontinuity) one will 
  probably gain from splitting up the interval and calling the integrator 
  on the subranges.  Perhaps a special-purpose integrator should be used.



In [33]:
susy_soln

 message: Solution found.
 success: True
  status: 0
     fun: 0.11901298086664347
       x: 0.007994208214256726
     nit: 15
    nfev: 15

In [34]:
plot_trigger(susy, susy_eff, susy_soln, "log")

In [35]:
susy_turnon = find_turnon(susy_eff, (100, 120))

In [36]:
susy_turnon

 message: 
          Optimization terminated successfully;
          The returned value satisfies the termination criteria
          (using xtol = 1.48e-08 )
 success: True
     fun: 4.169722389590902e-08
       x: 111.19166494393146
     nit: 27
    nfev: 30

In [37]:
tracking_eff, tracking_soln = fit_trigger(tracking, tracking_rate, [0.0001, 0.0080])

/var/folders/qc/b4ggx3516_qc8fy84rgtp36c0000gq/T/ipykernel_92722/2121129225.py:8: IntegrationWarning:

The maximum number of subdivisions (50) has been achieved.
  If increasing the limit yields no improvement it is advised to analyze 
  the integrand in order to determine the difficulties.  If the position of a 
  local difficulty can be determined (singularity, discontinuity) one will 
  probably gain from splitting up the interval and calling the integrator 
  on the subranges.  Perhaps a special-purpose integrator should be used.



In [38]:
tracking_soln

 message: Solution found.
 success: True
  status: 0
     fun: 6.415888883355703e-05
       x: 0.0007066113266013714
     nit: 13
    nfev: 13

In [39]:
plot_trigger(tracking, tracking_eff, tracking_soln, "log")

In [40]:
tracking_turnon = find_turnon(tracking_eff, (0, 10))

In [41]:
tracking_turnon

 message: 
          Optimization terminated successfully;
          The returned value satisfies the termination criteria
          (using xtol = 1.48e-08 )
 success: True
     fun: 5.101988276301483e-10
       x: 0.8443801147863089
     nit: 30
    nfev: 33

In [42]:
tau_eff, tau_soln = fit_trigger(tau, tau_rate, [0.0001, 0.0080])

/var/folders/qc/b4ggx3516_qc8fy84rgtp36c0000gq/T/ipykernel_92722/2121129225.py:8: IntegrationWarning:

The maximum number of subdivisions (50) has been achieved.
  If increasing the limit yields no improvement it is advised to analyze 
  the integrand in order to determine the difficulties.  If the position of a 
  local difficulty can be determined (singularity, discontinuity) one will 
  probably gain from splitting up the interval and calling the integrator 
  on the subranges.  Perhaps a special-purpose integrator should be used.



In [43]:
tau_soln

 message: Solution found.
 success: True
  status: 0
     fun: 1.2928500458489478e-05
       x: 0.0003294091518563356
     nit: 13
    nfev: 13

In [44]:
plot_trigger(tau, tau_eff, tau_soln)

In [45]:
tau_turnon = find_turnon(tau_eff, (0, 40))

In [46]:
tau_turnon

 message: 
          Optimization terminated successfully;
          The returned value satisfies the termination criteria
          (using xtol = 1.48e-08 )
 success: True
     fun: 4.532689446001825e-09
       x: 28.505134708115076
     nit: 29
    nfev: 32

# Modeling Skill

In [47]:
b2g_threshold = b2g_turnon.x
higgs_threshold = higgs_turnon.x
muon_threshold = muon_turnon.x
susy_threshold = susy_turnon.x
tracking_threshold = 2
tau_threshold = tau_turnon.x

In [48]:
#find the percentile of measurements above median acceptance level
b2g_prctile = exp_cdf(b2g_threshold, b2g_soln.x)
higgs_prctile = exp_cdf(higgs_threshold, higgs_soln.x)
muon_prctile = exp_cdf(muon_threshold, muon_soln.x)
susy_prctile = exp_cdf(susy_threshold, susy_soln.x)
tracking_prctile = exp_cdf(tracking_threshold, tracking_soln.x)
tau_prctile = exp_cdf(tau_threshold, tau_soln.x) 

In [49]:
effiencies = [b2g_eff, higgs_eff, muon_eff, susy_eff, tracking_eff, tau_eff]

In [50]:
fits = [b2g_soln.x, higgs_soln.x, muon_soln.x, susy_soln.x, tracking_soln.x, tau_soln.x]

In [51]:
thresholds = np.array([b2g_threshold, higgs_threshold, muon_threshold, susy_threshold, tracking_threshold, tau_threshold])

In [52]:
prctiles = np.array([b2g_prctile, higgs_prctile, muon_prctile, susy_prctile, tracking_prctile, tau_prctile])

In [53]:
prctiles

array([0.84773964, 0.48903578, 0.00719903, 0.58888789, 0.00141222,
       0.00934591])

In [54]:
def generate_null():
    #take a random trigger path
    path = np.random.choice(np.arange(len(thresholds)), p = rates_norm)
    p = np.random.uniform() * prctiles[path]
    l = fits[path]
    e = exp_generator(p, l)
    z = effiencies[path](e)
    
    return path, e, z


In [55]:
generate_null()

(np.int64(1), np.float64(152.23907108610138), array(0.))

In [56]:
null_evt = generate_null()

In [57]:
n_samples = int(1e5)

In [58]:
null_evts = np.stack([generate_null() for i in range(n_samples)])

In [59]:
null_evts.shape

(100000, 3)

In [60]:
null_evts

array([[1.00000000e+00, 8.06397137e+01, 0.00000000e+00],
       [0.00000000e+00, 2.38014938e+02, 2.10905967e-03],
       [1.00000000e+00, 1.88838560e+02, 0.00000000e+00],
       ...,
       [1.00000000e+00, 1.31631178e+01, 0.00000000e+00],
       [0.00000000e+00, 4.42770093e+01, 0.00000000e+00],
       [3.00000000e+00, 4.22034494e+00, 0.00000000e+00]])

In [61]:
np.std(null_evts[:,2])

np.float64(0.15845242697852324)

In [62]:
px.histogram(null_evts[:,2])

In [63]:
null_dist = ecdf(null_evts[:,2])

In [64]:
def generate_positive():
    #take a random trigger path
    path = np.random.choice(np.arange(len(thresholds)), p = rates_norm)
    p = 1.0 - np.random.uniform() * prctiles[path]
    l = fits[path]
    e = exp_generator(p, l)
    z = effiencies[path](e)
    
    return path, e, z



In [65]:
pos_evts = np.stack([generate_positive() for i in range(n_samples)])

In [66]:
px.histogram(pos_evts[:,2])

In [67]:
pos_dist = ecdf(pos_evts[:,2])

In [68]:
pos_dist.cdf.evaluate(0.5)

array(0.18709)

In [69]:
xs = np.linspace(0.0, 1.0, 101)
fig = go.Figure()
fig.add_scatter(x = xs, y = null_dist.cdf.evaluate(xs), name="Null")
fig.add_scatter(x = xs, y = pos_dist.cdf.evaluate(xs), name="Positive")